In [1]:
## Basic import and DF creation

import pandas as pd

# Specify the path to your Excel file
file_path = r"09_Outputs\main_data.xlsx"

# Load the Excel file into a DataFrame using the openpyxl engine
df_main = pd.read_excel(file_path, engine='openpyxl')

# Remove quotation marks from the 'Entity' column
df_main['Entity'] = df_main['Entity'].str.replace('"', '')

# Retrieve unique countries from the DataFrame and store them as a list of strings
all_countries = df_main['Entity'].drop_duplicates().astype(str).tolist()

# Display the first 5 rows of the DataFrame for a quick overview

# Assuming df_main is your dataframe

min_year = df_main["Year"].min()
max_year = df_main["Year"].max()

# ... Rest of your code ...

df_main.head()

Entity  Year Code  Annual CO₂ emissions  \
0  Afghanistan  1965  AFG             1006917.0   
1  Afghanistan  1966  AFG             1091159.0   
2  Afghanistan  1967  AFG             1281865.0   
3  Afghanistan  1968  AFG             1223391.0   
4  Afghanistan  1969  AFG              941232.0   

   Renewables (TWh growth - equivalent)  Annual CO₂ emissions from flaring  \
0                                   NaN                                0.0   
1                                   NaN                                0.0   
2                                   NaN                                0.0   
3                                   NaN                                0.0   
4                                   NaN                                0.0   

   Annual CO₂ emissions from gas  Annual CO₂ emissions from oil  \
0                            0.0                       542272.0   
1                            0.0                       575248.0   
2                       260144.0                       556928.0   
3                       347041.0                       496817.0   
4                            0.0                       527616.0   

   Annual CO₂ emissions from coal  Primary energy consumption (TWh)  ...  \
0                        381056.0                               NaN  ...   
1                        428688.0                               NaN  ...   
2                        399376.0                               NaN  ...   
3                        332429.0                               NaN  ...   
4                        362736.0                               NaN  ...   

   Electricity from fossil fuels (TWh)  \
0                                  NaN   
1                                  NaN   
2                                  NaN   
3                                  NaN   
4                                  NaN   

   Other renewables excluding bioenergy (TWh)  Oil consumption - TWh  \
0                                         NaN                    NaN   
1                                         NaN                    NaN   
2                                         NaN                    NaN   
3                                         NaN                    NaN   
4                                         NaN                    NaN   

   Primary energy consumption per GDP (kWh/$)  Low-carbon electricity (TWh)  \
0                                         NaN                           NaN   
1                                         NaN                           NaN   
2                                         NaN                           NaN   
3                                         NaN                           NaN   
4                                         NaN                           NaN   

   GDP (constant 2015 US$)  \
0                      NaN   
1                      NaN   
2                      NaN   
3                      NaN   
4                      NaN   

   Renewable electricity (% electricity production) (World Bank (2015))  \
0                                                NaN                      
1                                                NaN                      
2                                                NaN                      
3                                                NaN                      
4                                                NaN                      

   Solar photovoltaic capacity  \
0                          NaN   
1                          NaN   
2                          NaN   
3                          NaN   
4                          NaN   

   Annual greenhouse gas emissions in CO2 equivalents  \
0                                         24430504.0    
1                                         25174948.0    
2                                         24644464.0    
3                                         24382198.0    
4                                         23233260.0    

   Electricity from wind (TWh) 

In [ ]:
##################### Section 1: Imports and Data Assumptions #####################
import pandas as pd
import plotly.graph_objects as go
import ipywidgets as widgets
from IPython.display import display, clear_output

# Assuming df_main is already loaded
filtered_df = df_main

##################### Section 2: Helper Functions #####################
all_countries = sorted(df_main['Entity'].drop_duplicates().astype(str).tolist())
default_countries = ['Germany', 'China', 'India', 'United States', 'World']

def custom_sort(country):
    selected_countries = [cb.description for cb in checkboxes_container.children if cb.value]
    if country in default_countries:
        return (-2, default_countries.index(country))
    elif country in selected_countries:
        return (-1, selected_countries.index(country))
    else:
        return (1, country)

def update_country_list(*args):
    selected_countries = [cb.description for cb in checkboxes_container.children if cb.value]
    search_input = search_box.value
    search_results = [country for country in all_countries if search_input.lower() in country.lower()]
    updated_countries = list(set(search_results + selected_countries))
    
    updated_countries = sorted(updated_countries, key=custom_sort)
    
    updated_checkboxes = [widgets.Checkbox(value=(country in selected_countries), description=country,
                                           layout=widgets.Layout(width="100%", padding="0px")) for country in updated_countries]
    for cb in updated_checkboxes:
        cb.observe(plot_selected_column, names='value')
        cb.observe(update_country_list, names='value')
    checkboxes_container.children = tuple(updated_checkboxes)

def plot_selected_column(change=None):
    column = column_dropdown.value
    selected_countries = [cb.description for cb in checkboxes_container.children if cb.value]
    with out:
        clear_output(wait=True)
        fig = go.Figure()
        for country in selected_countries:
            country_data = filtered_df[filtered_df['Entity'] == country]
            fig.add_trace(go.Scatter(x=country_data['Year'], y=country_data[column], mode='lines', name=country, showlegend=True))
        
        fig.update_layout(title=column, 
                          xaxis=dict(title='Year', showgrid=True, gridcolor='rgba(128, 128, 128, 0.5)', gridwidth=0.5, griddash='dot', zeroline=False),
                          yaxis=dict(title=column, showgrid=True, gridcolor='rgba(128, 128, 128, 0.5)', gridwidth=0.5, griddash='dot', zeroline=False),
                          plot_bgcolor='white', paper_bgcolor='white')
        fig.show()

def clear_search(*args):
    search_box.value = ''

##################### Section 3: Create Widgets #####################
checkboxes_container = widgets.VBox([], layout=widgets.Layout(overflow_y="scroll", height="400px", border="1px solid #DDD"))

country_checkboxes = [widgets.Checkbox(value=(country in default_countries), description=country, layout=widgets.Layout(width="100%", padding="0px")) for country in sorted(all_countries, key=custom_sort)]
for cb in country_checkboxes:
    cb.observe(plot_selected_column, names='value')
    cb.observe(update_country_list, names='value')

checkboxes_container.children = tuple(country_checkboxes)

search_box = widgets.Text(value='', placeholder='Search for Countries...')
search_box.observe(update_country_list, names='value')

# Create the clear button and set its behavior
clear_button = widgets.Button(description="X")
clear_button.on_click(clear_search)



# Group the search box and clear button together
search_widget = widgets.HBox([search_box, clear_button])

out = widgets.Output(layout=widgets.Layout(width="60%"))
columns_to_plot = df_main.columns[df_main.columns.get_loc('Code')+1:]
column_dropdown = widgets.Dropdown(options=columns_to_plot, description='Select Column:')
column_dropdown.observe(plot_selected_column, names='value')

# Adjust the width of the dropdown
column_dropdown.layout.width = '30%'

checkboxes_container = widgets.VBox([], layout=widgets.Layout(overflow_y="scroll", height="400px", border="1px solid #DDD"))
country_checkboxes = [widgets.Checkbox(value=(country in default_countries), description=country, layout=widgets.Layout(width="100%", padding="0px")) for country in sorted(all_countries, key=custom_sort)]
for cb in country_checkboxes:
    cb.observe(plot_selected_column, names='value')
    cb.observe(update_country_list, names='value')
checkboxes_container.children = tuple(country_checkboxes)

search_box = widgets.Text(value='', placeholder='Search for Countries...')
search_box.observe(update_country_list, names='value')

clear_button = widgets.Button(description="X")
clear_button.on_click(clear_search)
search_widget = widgets.HBox([search_box, clear_button])

out = widgets.Output(layout=widgets.Layout(width="60%"))

# Displaying widgets
left_container = widgets.VBox([search_widget, checkboxes_container])
display(column_dropdown)
display(widgets.HBox([left_container, out]))
plot_selected_column()
update_country_list()  # initialize the country list

In [ ]:
import dash
from dash import dcc, html
from dash.dependencies import Input, Output
import plotly.express as px
import pandas as pd

# Assuming df_main is your dataframe
df_main = df_main[~df_main['Entity'].isin(['World', 'Continent'])]

app = dash.Dash(__name__)

# Create a dropdown list with available columns (starting from the 4th column)
dropdown_options = df_main.columns[3:].tolist()

def generate_color_steps(df, selected_column, n_steps=5):
    min_val = df[selected_column].min()
    max_val = df[selected_column].max()
    step_size = (max_val - min_val) / n_steps
    steps = [min_val + i * step_size for i in range(n_steps)]
    color_scale = px.colors.sequential.Reds
    return {step: color_scale[i] for i, step in enumerate(steps)}

def get_latest_figure(selected_column, initial_year=None):
    df = df_main[df_main[selected_column].notnull()]
    df = df[~df['Entity'].isin(['World', 'Continent'])]

    # Use the provided initial_year or determine the max year
    year_to_display = initial_year if initial_year else df["Year"].max()

    color_map = generate_color_steps(df, selected_column)

    fig = px.choropleth(df[df["Year"] == year_to_display], 
                        locations="Code",
                        color=selected_column,
                        hover_name="Entity",
                        color_discrete_map=color_map,
                        labels={selected_column: selected_column},
                        title=f'Choropleth Map of {selected_column}')

    fig.update_geos(showframe=False, showcoastlines=False, projection_type='equirectangular')
    return fig

app.layout = html.Div([
    dcc.Dropdown(
        id='column_dropdown',
        options=[{'label': i, 'value': i} for i in dropdown_options],
        value=dropdown_options[0],
        clearable=False,
        searchable=False
    ),
    dcc.Graph(
        id='choropleth_map', 
        figure=get_latest_figure(dropdown_options[0]),
        style={"height": "70vh", "width": "124.5vh"}
    ),
])

def generate_color_steps(df, selected_column, n_steps=5):
    min_val = df[selected_column].min()
    max_val = df[selected_column].max()
    step_size = (max_val - min_val) / n_steps
    steps = [min_val + i * step_size for i in range(n_steps)]
    color_scale = px.colors.sequential.Reds
    return {step: color_scale[i] for i, step in enumerate(steps)}

@app.callback(
    Output('choropleth_map', 'figure'),
    [Input('column_dropdown', 'value')]
)
def update_figure(selected_column):
    df = df_main[df_main[selected_column].notnull()]
    df = df[~df['Entity'].isin(['World', 'Continent'])]

    color_map = generate_color_steps(df, selected_column)
    
    fig = px.choropleth(df, 
                        locations="Code",
                        color=selected_column,
                        hover_name="Entity",
                        animation_frame="Year",
                        color_discrete_map=color_map,
                        labels={selected_column: selected_column},
                        title=f'Choropleth Map of {selected_column}')

    fig.update_geos(showframe=False, showcoastlines=False, projection_type='equirectangular')

    # Erhalten Sie den Namen des letzten Frames (maximales Jahr)
    last_frame_name = fig.frames[-1].data

    # Erstellen Sie die Schritte für den Slider
    slider_steps = []
    for frame in fig.frames:
        step = dict(args=[[frame.name], 
                          {"frame": {"duration": 500, "redraw": True},
                           "mode": "immediate",
                           "transition": {"duration": 0}}],
                    label=frame.name,
                    method="animate")
        slider_steps.append(step)

    # Update Slider-Einstellungen
    fig.layout.update(sliders=[{
        'active': len(fig.frames) - 1,  # Setzen Sie den aktiven Schritt auf den letzten Schritt
        'yanchor': 'top',
        'xanchor': 'left',
        'currentvalue': {
            'font': {'size': 20},
            'prefix': 'Year:',
            'visible': True,
            'xanchor': 'right'
        },
        'transition': {'duration': 500, 'easing': 'cubic-in-out'},
        'pad': {'b': 10, 't': 50},
        'len': 0.9,
        'x': 0.1,
        'y': 0,
        'steps': slider_steps  # Zuweisung der Schritte zum Slider
    }])

    fig.layout.sliders[0].steps[-1]["args"][1]["frame"]["duration"] = 0
    fig.layout.sliders[0].steps[-1]["args"][1]["transition"]["duration"] = 0

    return fig

if __name__ == '__main__':
    app.run_server(debug=True, port=8051)



In [ ]:
import pandas as pd
import dash
from dash import dcc, html
from dash.dependencies import Input, Output
import plotly.express as px
import plotly.graph_objs as go


# Exclude 'World' and continents from the main dataframe
excluded_entities = ['World', 'Asia', 'Africa', 'Europe', 'North America', 'South America', 'Oceania', 'Antarctica']
df_main = df_main[~df_main['Entity'].isin(excluded_entities)]

# Create a dropdown list with available columns (starting from the 4th column)
dropdown_options = df_main.columns[3:].tolist()

def get_end_year_for_column(column):
    """
    Get the latest year where any country has a non-zero value for the given column.
    """
    non_zero_rows = df_main[df_main[column].notnull() & (df_main[column] != 0)]
    if not non_zero_rows.empty:
        return non_zero_rows["Year"].max()
    else:
        return df_main["Year"].max()

def generate_color_steps(df, selected_column, n_steps=5):
    min_val = df[selected_column].min()
    max_val = df[selected_column].max()
    step_size = (max_val - min_val) / n_steps
    steps = [min_val + i * step_size for i in range(n_steps)]
    color_scale = px.colors.sequential.Reds
    return {step: color_scale[i] for i, step in enumerate(steps)}


app = dash.Dash(__name__)

app.layout = html.Div([
    dcc.Dropdown(
        id='column_dropdown',
        options=[{'label': i, 'value': i} for i in dropdown_options],
        value=dropdown_options[0],
        clearable=False,
        searchable=False
    ),
    dcc.Graph(
        id='choropleth_map', 
        figure=get_latest_figure(dropdown_options[0]),
        style={"height": "70vh", "width": "124.5vh"}
    ),
])

def get_latest_figure(selected_column):
    df = df_main[df_main[selected_column].notnull()]
    # Dynamically set the year to display based on the column
    year_to_display = get_end_year_for_column(selected_column)
    color_map = generate_color_steps(df, selected_column)
    fig = px.choropleth(df[df["Year"] == year_to_display], 
                        locations="Code",
                        color=selected_column,
                        hover_name="Entity",
                        color_discrete_map=color_map,
                        labels={selected_column: selected_column},
                        title=f'Choropleth Map of {selected_column}')
    fig.update_geos(showframe=False, showcoastlines=False, projection_type='equirectangular')
    return fig

@app.callback(
    Output('choropleth_map', 'figure'),
    [Input('column_dropdown', 'value')]
)
def update_figure(selected_column):
    df = df_main[df_main[selected_column].notnull()]
    color_map = generate_color_steps(df, selected_column)
    
    # Set the end year based on the column
    end_year = get_end_year_for_column(selected_column)
    
    # Create the initial figure with the data for the end year
    fig = px.choropleth(df[df["Year"] == end_year], 
                        locations="Code",
                        color=selected_column,
                        hover_name="Entity",
                        color_discrete_map=color_map,
                        labels={selected_column: selected_column},
                        title=f'Choropleth Map of {selected_column}')
    
    # Add animation frames
    v_max = max(color_map.keys())
    frames = []
    for year in df["Year"].unique():
        temp_fig = px.choropleth(
            df[df["Year"] == year], 
            locations="Code",
            color=selected_column,
            hover_name="Entity",
            color_discrete_map=color_map
        )
        frame_data = temp_fig.data[0]
        frames.append(
            go.Frame(
                data=go.Choropleth(
                    locations=frame_data['locations'],
                    z=frame_data['z'],
                    colorscale=[[k/v_max, v] for k, v in color_map.items()],
                    zmin=0,
                    zmax=v_max
                ),
                name=str(year)
            )
        )


    fig.frames = frames

    fig.update_geos(showframe=False, showcoastlines=False, projection_type='equirectangular')

    # Create slider steps and find the index of the end year
    slider_steps = []
    end_year_index = 0
    for index, frame in enumerate(fig.frames):
        step = dict(args=[[frame.name], 
                          {"frame": {"duration": 500, "redraw": True},
                           "mode": "immediate",
                           "transition": {"duration": 0}}],
                    label=frame.name,
                    method="animate")
        slider_steps.append(step)
        if frame.name == str(end_year):
            end_year_index = index

    # Update slider settings with the end year's index as the active step
    fig.update_layout(sliders=[{
        'active': end_year_index,
        'yanchor': 'top',
        'xanchor': 'left',
        'currentvalue': {
            'font': {'size': 20},
            'prefix': 'Year:',
            'visible': True,
            'xanchor': 'right'
        },
        'transition': {'duration': 500, 'easing': 'cubic-in-out'},
        'pad': {'b': 10, 't': 50},
        'len': 0.9,
        'x': 0.1,
        'y': 0,
        'steps': slider_steps
    }])

    return fig
if __name__ == '__main__':
    app.run_server(debug=True, port=8051)


In [ ]:
import pandas as pd
import dash
from dash import dcc, html
from dash.dependencies import Input, Output
import plotly.express as px
import plotly.graph_objs as go

# Assuming df_main is your dataframe
# Exclude 'World' and continents from the main dataframe
df_main = df_main[~df_main['Entity'].isin(['World', 'Asia', 'Africa', 'Europe', 'North America', 'South America', 'Oceania', 'Antarctica'])]

# Create a dropdown list with available columns (starting from the 4th column)
dropdown_options = df_main.columns[3:].tolist()

# Generate color steps based on the data range
def generate_color_steps(df, selected_column, n_steps=5):
    min_val = df[selected_column].min()
    max_val = df[selected_column].max()
    step_size = (max_val - min_val) / n_steps
    steps = [min_val + i * step_size for i in range(n_steps)]
    color_scale = px.colors.sequential.Reds
    return {step: color_scale[i] for i, step in enumerate(steps)}

# Get the latest year for a given column where data is non-zero
def get_end_year_for_column(column):
    non_zero_rows = df_main[df_main[column].notnull() & (df_main[column] != 0)]
    if not non_zero_rows.empty:
        return non_zero_rows["Year"].max()
    else:
        return df_main["Year"].max()

# Generate the choropleth figure for the latest year
def get_latest_figure(selected_column):
    df = df_main[df_main[selected_column].notnull()]
    year_to_display = get_end_year_for_column(selected_column)
    color_map = generate_color_steps(df, selected_column)
    fig = px.choropleth(df[df["Year"] == year_to_display], 
                        locations="Code",
                        color=selected_column,
                        hover_name="Entity",
                        color_discrete_map=color_map,
                        labels={selected_column: selected_column},
                        title=f'Choropleth Map of {selected_column}')
    fig.update_geos(showframe=False, showcoastlines=False, projection_type='equirectangular')
    update_year_annotation(fig, year_to_display)
    return fig

# Update the annotation to display the current year
def update_year_annotation(fig, year):
    fig.update_layout(
        annotations=[
            dict(
                x=0.5,
                y=0.95,
                xref="paper",
                yref="paper",
                text=f"Year: {year}",
                showarrow=False,
                font=dict(size=20)
            )
        ]
    )

app = dash.Dash(__name__)

app.layout = html.Div([
    dcc.Dropdown(
        id='column_dropdown',
        options=[{'label': i, 'value': i} for i in dropdown_options],
        value=dropdown_options[0],
        clearable=False,
        searchable=False
    ),
    dcc.Graph(
        id='choropleth_map', 
        figure=get_latest_figure(dropdown_options[0]),
        style={"height": "80vh", "width": "130vh"},
        config={'toImageButtonOptions': {'scale': 2}}  # Increase pixel density for download
    ),
])

@app.callback(
    Output('choropleth_map', 'figure'),
    [Input('column_dropdown', 'value')]
)
def update_figure(selected_column):
    df = df_main[df_main[selected_column].notnull()]
    color_map = generate_color_steps(df, selected_column)
    
    end_year = get_end_year_for_column(selected_column)  # Get the latest year for the column
    
    fig = px.choropleth(df, 
                        locations="Code",
                        color=selected_column,
                        hover_name="Entity",
                        hover_data={"Year": True},  # Add year to hover data
                        animation_frame="Year",
                        color_discrete_map=color_map,
                        labels={selected_column: selected_column},
                        title=f'Choropleth Map of {selected_column}')

    fig.update_geos(showframe=False, showcoastlines=False, projection_type='equirectangular')


    # Add play and pause buttons
    fig.update_layout(
        updatemenus=[{
            'buttons': [
                {
                    'args': [None, {'frame': {'duration': 500, 'redraw': True}, 'fromcurrent': True, 'transition': {'duration': 0}}],
                    'label': 'Play',
                    'method': 'animate'
                },
                {
                    'args': [[None], {'frame': {'duration': 0, 'redraw': True}, 'mode': 'immediate', 'transition': {'duration': 0}}],
                    'label': 'Pause',
                    'method': 'animate'
                }
            ],
            'direction': 'left',
            'pad': {'r': 10, 't': 87},
            'showactive': False,
            'type': 'buttons',
            'x': 0.1,
            'xanchor': 'right',
            'y': 0,
            'yanchor': 'top'
        }]
    )
    # Ensure the latest year frame is the last frame and start the animation there
    sorted_frames = sorted(fig.frames, key=lambda x: x.name)
    fig.frames = sorted_frames[:-1] + [f for f in sorted_frames if f.name == str(end_year)]


    return fig

if __name__ == '__main__':
    app.run_server(debug=True, port=8051)
### runs perfect, but last 

In [ ]:
import pandas as pd
import dash
from dash import dcc, html
from dash.dependencies import Input, Output
import plotly.express as px
import plotly.graph_objs as go

# Assuming df_main is your dataframe
df_main = df_main[~df_main['Entity'].isin(['World', 'Asia', 'Africa', 'Europe', 'North America', 'South America', 'Oceania', 'Antarctica'])]


# Exclude 'World' and continents from the main dataframe
#excluded_entities = ['World', 'Asia', 'Africa', 'Europe', 'North America', 'South America', 'Oceania', 'Antarctica']
#df_main = df_main[~df_main['Entity'].isin(excluded_entities)]

# Create a dropdown list with available columns (starting from the 4th column)
dropdown_options = df_main.columns[3:].tolist()

def get_end_year_for_column(column):
    non_zero_rows = df_main[df_main[column].notnull() & (df_main[column] != 0)]
    if not non_zero_rows.empty:
        return non_zero_rows["Year"].max()
    else:
        return df_main["Year"].max()

def generate_color_steps(df, selected_column, n_steps=5):
    min_val = df[selected_column].min()
    max_val = df[selected_column].max()
    step_size = (max_val - min_val) / n_steps
    steps = [min_val + i * step_size for i in range(n_steps)]
    color_scale = px.colors.sequential.Reds
    return {step: color_scale[i] for i, step in enumerate(steps)}

def update_year_annotation(fig, year):
    fig.update_layout(
        annotations=[
            dict(
                x=0.5,
                y=0.95,
                xref="paper",
                yref="paper",
                text=f"Year: {year}",
                showarrow=False,
                font=dict(size=20)
            )
        ]
    )

app = dash.Dash(__name__)

app.layout = html.Div([
    dcc.Dropdown(
        id='column_dropdown',
        options=[{'label': i, 'value': i} for i in dropdown_options],
        value=dropdown_options[0],
        clearable=False,
        searchable=False
    ),
    dcc.Graph(
        id='choropleth_map', 
        figure=get_latest_figure(dropdown_options[0]),
        style={"height": "80vh", "width": "130vh"},
        config={'toImageButtonOptions': {'scale': 2}}  # Increase pixel density for download
    ),
])

def get_latest_figure(selected_column):
    df = df_main[df_main[selected_column].notnull()]
    year_to_display = get_end_year_for_column(selected_column)
    color_map = generate_color_steps(df, selected_column)
    fig = px.choropleth(df[df["Year"] == year_to_display], 
                        locations="Code",
                        color=selected_column,
                        hover_name="Entity",
                        color_discrete_map=color_map,
                        labels={selected_column: selected_column},
                        title=f'Choropleth Map of {selected_column}')
    fig.update_geos(showframe=False, showcoastlines=False, projection_type='equirectangular')
    update_year_annotation(fig, year_to_display)
    return fig

@app.callback(
    Output('choropleth_map', 'figure'),
    [Input('column_dropdown', 'value')]
)
def update_figure(selected_column):
    df = df_main[df_main[selected_column].notnull()]
    color_map = generate_color_steps(df, selected_column)
    
    fig = px.choropleth(df, 
                        locations="Code",
                        color=selected_column,
                        hover_name="Entity",
                        hover_data={"Year": True},  # Add year to hover data
                        animation_frame="Year",
                        color_discrete_map=color_map,
                        labels={selected_column: selected_column},
                        title=f'Choropleth Map of {selected_column}')

    fig.update_geos(showframe=False, showcoastlines=False, projection_type='equirectangular')

    # Add play and pause buttons
    fig.update_layout(
        updatemenus=[{
            'buttons': [
                {
                    'args': [None, {'frame': {'duration': 500, 'redraw': True}, 'fromcurrent': True, 'transition': {'duration': 0}}],
                    'label': 'Play',
                    'method': 'animate'
                },
                {
                    'args': [[None], {'frame': {'duration': 0, 'redraw': True}, 'mode': 'immediate', 'transition': {'duration': 0}}],
                    'label': 'Pause',
                    'method': 'animate'
                }
            ],
            'direction': 'left',
            'pad': {'r': 10, 't': 87},
            'showactive': False,
            'type': 'buttons',
            'x': 0.1,
            'xanchor': 'right',
            'y': 0,
            'yanchor': 'top'
        }]
    )

    return fig

if __name__ == '__main__':
    app.run_server(debug=True, port=8051)

In [ ]:
import pandas as pd
import dash
from dash import dcc, html
from dash.dependencies import Input, Output
import plotly.express as px
import plotly.graph_objs as go

# Assuming df_main is your dataframe
# Exclude 'World' and continents from the main dataframe
df_main = df_main[~df_main['Entity'].isin(['World', 'Asia', 'Africa', 'Europe', 'North America', 'South America', 'Oceania', 'Antarctica'])]

# Create a dropdown list with available columns (starting from the 4th column)
dropdown_options = df_main.columns[3:].tolist()

# Generate color steps based on the data range
def generate_color_steps(df, selected_column, n_steps=5):
    min_val = df[selected_column].min()
    max_val = df[selected_column].max()
    step_size = (max_val - min_val) / n_steps
    steps = [min_val + i * step_size for i in range(n_steps)]
    color_scale = px.colors.sequential.Reds
    return {step: color_scale[i] for i, step in enumerate(steps)}

# Get the latest year for a given column where data is non-zero
def get_end_year_for_column(column):
    non_zero_rows = df_main[df_main[column].notnull() & (df_main[column] != 0)]
    if not non_zero_rows.empty:
        return non_zero_rows["Year"].max()
    else:
        return df_main["Year"].max()

# Generate the choropleth figure for the latest year
def get_latest_figure(selected_column):
    df = df_main[df_main[selected_column].notnull()]
    year_to_display = get_end_year_for_column(selected_column)
    color_map = generate_color_steps(df, selected_column)
    fig = px.choropleth(df[df["Year"] == year_to_display], 
                        locations="Code",
                        color=selected_column,
                        hover_name="Entity",
                        color_discrete_map=color_map,
                        labels={selected_column: selected_column},
                        title=f'Choropleth Map of {selected_column}')
    fig.update_geos(showframe=False, showcoastlines=False, projection_type='equirectangular')
    update_year_annotation(fig, year_to_display)
    return fig

# Update the annotation to display the current year
def update_year_annotation(fig, year):
    fig.update_layout(
        annotations=[
            dict(
                x=0.5,
                y=0.95,
                xref="paper",
                yref="paper",
                text=f"Year: {year}",
                showarrow=False,
                font=dict(size=20)
            )
        ]
    )

app = dash.Dash(__name__)

app.layout = html.Div([
    dcc.Dropdown(
        id='column_dropdown',
        options=[{'label': i, 'value': i} for i in dropdown_options],
        value=dropdown_options[0],
        clearable=False,
        searchable=False
    ),
    dcc.Graph(
        id='choropleth_map', 
        figure=get_latest_figure(dropdown_options[0]),
        style={"height": "80vh", "width": "130vh"},
        config={'toImageButtonOptions': {'scale': 2}}  # Increase pixel density for download
    ),
])

@app.callback(
    Output('choropleth_map', 'figure'),
    [Input('column_dropdown', 'value')]
)
# Extracting the relevant part of the second script and making the necessary modification
# The change will be in the update_figure function

def update_figure(selected_column):
    end_year = get_end_year_for_column(selected_column)  # Get the latest year for the column
    df_filtered = df_main[df_main["Year"] <= end_year]
    color_map = generate_color_steps(df_filtered, selected_column)
    
    fig = px.choropleth(df_filtered, 
                        locations="Code",
                        color=selected_column,
                        hover_name="Entity",
                        hover_data={"Year": True},
                        animation_frame="Year",
                        color_discrete_map=color_map,
                        labels={selected_column: selected_column},
                        title=f'Choropleth Map of {selected_column}')

    fig.update_geos(showframe=False, showcoastlines=False, projection_type='equirectangular')

    # Add play and pause buttons
    fig.update_layout(
        updatemenus=[{
            'buttons': [
                {
                    'args': [None, {'frame': {'duration': 500, 'redraw': True}, 'fromcurrent': True, 'transition': {'duration': 0}}],
                    'label': 'Play',
                    'method': 'animate'
                },
                {
                    'args': [[None], {'frame': {'duration': 0, 'redraw': True}, 'mode': 'immediate', 'transition': {'duration': 0}}],
                    'label': 'Pause',
                    'method': 'animate'
                }
            ],
            'direction': 'left',
            'pad': {'r': 10, 't': 87},
            'showactive': False,
            'type': 'buttons',
            'x': 0.1,
            'xanchor': 'right',
            'y': 0,
            'yanchor': 'top'
        }]
    )

    # Set the slider to start at the end year
    fig.update_layout(
        sliders=[{
            'steps': [
                {
                    'args': [
                        [f.name],
                        {
                            'frame': {'duration': 300, 'redraw': True},
                            'mode': 'immediate',
                            'transition': {'duration': 300}
                        }
                    ],
                    'label': f.name,
                    'method': 'animate'
                }
                for f in fig.frames
            ],
            'active': fig.frames[-1].name  # Set the active (starting) frame to the latest year
        }]
    )

    return fig



if __name__ == '__main__':
    app.run_server(debug=True, port=8051)
### df with error

In [ ]:
import pandas as pd
import dash
from dash import dcc, html
from dash.dependencies import Input, Output
import plotly.express as px
import plotly.graph_objs as go

# Assuming df_main is your dataframe
# Exclude 'World' and continents from the main dataframe
df_main = df_main[~df_main['Entity'].isin(['World', 'Asia', 'Africa', 'Europe', 'North America', 'South America', 'Oceania', 'Antarctica'])]

# Create a dropdown list with available columns (starting from the 4th column)
dropdown_options = df_main.columns[3:].tolist()

# Generate color steps based on the data range
def generate_color_steps(df, selected_column, n_steps=5):
    min_val = df[selected_column].min()
    max_val = df[selected_column].max()
    step_size = (max_val - min_val) / n_steps
    steps = [min_val + i * step_size for i in range(n_steps)]
    color_scale = px.colors.sequential.Reds
    return {step: color_scale[i] for i, step in enumerate(steps)}

# Get the latest year for a given column where data is non-zero
def get_end_year_for_column(column):
    non_zero_rows = df_main[df_main[column].notnull() & (df_main[column] != 0)]
    if not non_zero_rows.empty:
        return non_zero_rows["Year"].max()
    else:
        return df_main["Year"].max()

# Generate the choropleth figure for the latest year
def get_latest_figure(selected_column):
    df = df_main[df_main[selected_column].notnull()]
    year_to_display = get_end_year_for_column(selected_column)
    color_map = generate_color_steps(df, selected_column)
    fig = px.choropleth(df[df["Year"] == year_to_display], 
                        locations="Code",
                        color=selected_column,
                        hover_name="Entity",
                        color_discrete_map=color_map,
                        labels={selected_column: selected_column},
                        title=f'Choropleth Map of {selected_column}')
    fig.update_geos(showframe=False, showcoastlines=False, projection_type='equirectangular')
    update_year_annotation(fig, year_to_display)
    return fig

# Update the annotation to display the current year
def update_year_annotation(fig, year):
    fig.update_layout(
        annotations=[
            dict(
                x=0.5,
                y=0.95,
                xref="paper",
                yref="paper",
                text=f"Year: {year}",
                showarrow=False,
                font=dict(size=20)
            )
        ]
    )

app = dash.Dash(__name__)

app.layout = html.Div([
    dcc.Dropdown(
        id='column_dropdown',
        options=[{'label': i, 'value': i} for i in dropdown_options],
        value=dropdown_options[0],
        clearable=False,
        searchable=False
    ),
    dcc.Graph(
        id='choropleth_map', 
        figure=get_latest_figure(dropdown_options[0]),
        style={"height": "80vh", "width": "130vh"},
        config={'toImageButtonOptions': {'scale': 2}}  # Increase pixel density for download
    ),
])

@app.callback(
    Output('choropleth_map', 'figure'),
    [Input('column_dropdown', 'value'),
     Input('year_slider', 'value')]
)
def update_figure(selected_column, selected_year):
    df_filtered = df_main[df_main["Year"] <= selected_year]
    color_map = generate_color_steps(df_filtered, selected_column)
    
    # Filter the data by the selected year
    df_filtered = df_filtered[df_filtered['Year'] == selected_year]
    
    fig = px.choropleth(df_filtered, 
                        locations="Code",
                        color=selected_column,
                        hover_name="Entity",
                        hover_data={"Year": True},
                        color_discrete_map=color_map,
                        labels={selected_column: selected_column},
                        title=f'Choropleth Map of {selected_column}')

    fig.update_geos(showframe=False, showcoastlines=False, projection_type='equirectangular')

    # Add play and pause buttons
    fig.update_layout(
        updatemenus=[{
            'buttons': [
                {
                    'args': [None, {'frame': {'duration': 500, 'redraw': True}, 'fromcurrent': True, 'transition': {'duration': 0}}],
                    'label': 'Play',
                    'method': 'animate'
                },
                {
                    'args': [[None], {'frame': {'duration': 0, 'redraw': True}, 'mode': 'immediate', 'transition': {'duration': 0}}],
                    'label': 'Pause',
                    'method': 'animate'
                }
            ],
            'direction': 'left',
            'pad': {'r': 10, 't': 87},
            'showactive': False,
            'type': 'buttons',
            'x': 0.1,
            'xanchor': 'right',
            'y': 0,
            'yanchor': 'top'
        }]
    )

    # Set the slider to start at the end year
    fig.update_layout(
    sliders=[{
        'steps': [
            {
                'args': [
                    [f.name],
                    {
                        'frame': {'duration': 300, 'redraw': True},
                        'mode': 'immediate',
                        'transition': {'duration': 300}
                    }
                ],
                'label': f.name,
                'method': 'animate'
            }
            for f in fig.frames
        ],
        'active': 0,
        'pad': {'t': 50},
    }])

    # Update the annotation to display the current year
    update_year_annotation(fig, selected_year)

    return fig
if __name__ == '__main__':
    app.run_server(debug=True, port=8051)


In [ ]:
df_main.describe()

In [ ]:
print(df_main.dtypes)

In [8]:
import pandas as pd
import dash
from dash.dependencies import Input, Output
import plotly.express as px
import plotly.graph_objs as go
from dash import Dash, dcc, html

file_path = r"09_Outputs\main_data.xlsx"

# Load the Excel file into a DataFrame using the openpyxl engine
df_main = pd.read_excel(file_path, engine='openpyxl')

# Remove quotation marks from the 'Entity' column
df_main['Entity'] = df_main['Entity'].str.replace('"', '')

# Retrieve unique countries from the DataFrame and store them as a list of strings
all_countries = df_main['Entity'].drop_duplicates().astype(str).tolist()

# Assuming df_main is your dataframe
min_year = df_main["Year"].min()
max_year = df_main["Year"].max()

start_date = max_year

# Exclude 'World' and continents from the main dataframe
df_main = df_main[~df_main['Entity'].isin(['World', 'Asia', 'Africa', 'Europe', 'North America', 'South America', 'Oceania', 'Antarctica'])]

# Create a dropdown list with available columns (starting from the 4th column)
dropdown_options = df_main.columns[3:].tolist()

# Generate color steps based on the data range
def generate_color_steps(df, selected_column, n_steps=5):
    min_val = df[selected_column].min()
    max_val = df[selected_column].max()
    step_size = (max_val - min_val) / n_steps
    steps = [min_val + i * step_size for i in range(n_steps)]
    color_scale = px.colors.sequential.Reds
    return {step: color_scale[i] for i, step in enumerate(steps)}

# Get the latest year for a given column where data is non-zero
# Get the latest year for a given column where data is non-zero
def get_end_year_for_column(column):
    non_zero_rows = df_main[df_main[column].notnull() & (df_main[column] != 0)]
    if not non_zero_rows.empty:
        return non_zero_rows["Year"].max()
    else:
        return df_main["Year"].min()  # Use the minimum year in the dataset
    
# Generate the choropleth figure for the latest year
def get_latest_figure(selected_column):
    df = df_main[df_main[selected_column].notnull()]
    year_to_display = get_end_year_for_column(selected_column)
    color_map = generate_color_steps(df, selected_column)
    fig = px.choropleth(df[df["Year"] == year_to_display], 
                        locations="Code",
                        color=selected_column,
                        hover_name="Entity",
                        color_discrete_map=color_map,
                        labels={selected_column: selected_column},
                        title=f'Choropleth Map of {selected_column}')
    fig.update_geos(showframe=False, showcoastlines=False, projection_type='equirectangular')
    update_year_annotation(fig, year_to_display)
    return fig

# Update the annotation to display the current year
def update_year_annotation(fig, year):
    fig.update_layout(
        annotations=[
            dict(
                x=0.5,
                y=0.95,
                xref="paper",
                yref="paper",
                text=f"Year: {year}",
                showarrow=False,
                font=dict(size=20)
            )
        ]
    )

app = dash.Dash(__name__)

app.layout = html.Div([
    dcc.Dropdown(
        id='column_dropdown',
        options=[{'label': i, 'value': i} for i in dropdown_options],
        value=dropdown_options[0],
        clearable=False,
        searchable=False
    ),
    dcc.Graph(
        id='choropleth_map', 
        figure=get_latest_figure(dropdown_options[0]),
        style={"height": "80vh", "width": "130vh"},
        config={'toImageButtonOptions': {'scale': 2}}  # Increase pixel density for download
    ),
])

@app.callback(
    Output('choropleth_map', 'figure'),
    [Input('column_dropdown', 'value')]
)
def update_figure(selected_column):
    end_year = get_end_year_for_column(selected_column)
    df_filtered = df_main[df_main["Year"] <= end_year]
    color_map = generate_color_steps(df_filtered, selected_column)
    
    fig = px.choropleth(df_filtered, 
                        locations="Code",
                        color=selected_column,
                        hover_name="Entity",
                        hover_data={"Year": True},
                        animation_frame="Year",
                        color_discrete_map=color_map,
                        labels={selected_column: selected_column},
                        title=f'Choropleth Map of {selected_column}')

    fig.update_geos(showframe=False, showcoastlines=False, projection_type='equirectangular')

    fig.update_layout(
        sliders=[{
            'steps': [
                {
                    'args': [
                        [f.name],
                        {
                            'frame': {'duration': 300, 'redraw': True},
                            'mode': 'immediate',
                            'transition': {'duration': 300}
                        }
                    ],
                    'label': f.name,
                    'method': 'animate'
                }
                for f in fig.frames
            ],
            'active': int(end_year),  # Convert end_year to an integer
            'max': int(get_end_year_for_column(selected_column))  # Set the maximum value of the slider
        }]
    )

    return fig

if __name__ == '__main__':
    app.run_server(debug=True, port=8051)
    
print("Start date after initialization:", start_date)

# ... Rest of your code ...

print("Start date before returning the figure object:", start_date)

Start date after initialization: 2022
Start date before returning the figure object: 2022
---------------------------------------------------------------------------
ValueError                                Traceback (most recent call last)
File ~\anaconda3\envs\pythonkurs\Lib\site-packages\plotly\graph_objs\_figure.py:775, in Figure.update_layout(
    self=Figure({
    'data': [{'coloraxis': 'coloraxis',...                           'yanchor': 'top'}]}
}),
    dict1=None,
    overwrite=False,
    **kwargs={'sliders': [{'active': 2021, 'max': 2021, 'steps': [{'args': [[...], {...}], 'label': '1965', 'method': 'animate'}, {'args': [[...], {...}], 'label': '1966', 'method': 'animate'}, {'args': [[...], {...}], 'label': '1967', 'method': 'animate'}, {'args': [[...], {...}], 'label': '1968', 'method': 'animate'}, {'args': [[...], {...}], 'label': '1969', 'method': 'animate'}, {'args': [[...], {...}], 'label': '1970', 'method': 'animate'}, {'args': [[...], {...}], 'label': '1971', 'method'